In [17]:
import pandas as pd
import numpy as np
import xgboost as xgb
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split, GridSearchCV 
from sklearn.metrics import make_scorer, classification_report, make_scorer, recall_score, f1_score
from sklearn.feature_extraction.text import TfidfVectorizer
from DST_fun import review_vector
from DST_model_report import model_report

# importing training set
train = pd.read_csv("../data/avis/train_noYC_lemma_sent_equil.csv", index_col=0)
# split between features(X) and target(y)
y_train = train.etoiles -1 # les classes doivent commencer à 0, remettre +1 pour interpretation!
X_train = train.drop("etoiles", axis = 1)
X_train = X_train[['n_avis','sentiment_norm','longueur_texte']]

# importing test set
test = pd.read_csv('../data/avis/test_noYC_lemma_sent_equil.csv')
# split between features(X) and target(y)
X_test = test.drop("etoiles", axis =1)
X_test = X_test[['n_avis','sentiment_norm','longueur_texte']]
y_test = test['etoiles'] -1 # les classes doivent commencer à 0, remettre +1 pour interpretation!
X_train.head(3)

ImportError: cannot import name 'model_report' from 'DST_model_report' (/Users/lheyerda/Library/CloudStorage/OneDrive-InstitutPasteurParis/github/juil23_cds_supply_chain/notebooks/DST_model_report.py)

In [7]:

train =xgb.DMatrix(data= X_train,label = y_train)
test = xgb.DMatrix(data= X_test, label = y_test)
params = {'booster': 'gbtree', 'learning_rate': 0.1, 'objective': 'multi:softmax', 'num_class' : 5}
xgb1 = xgb.train(params=params, dtrain=train, num_boost_round=100, evals=[(train, 'train'), (test, 'eval')])

[0]	train-mlogloss:1.58185	eval-mlogloss:1.58629
[1]	train-mlogloss:1.55771	eval-mlogloss:1.56647
[2]	train-mlogloss:1.53629	eval-mlogloss:1.54870
[3]	train-mlogloss:1.51729	eval-mlogloss:1.53364
[4]	train-mlogloss:1.50081	eval-mlogloss:1.52012
[5]	train-mlogloss:1.48546	eval-mlogloss:1.50839
[6]	train-mlogloss:1.47168	eval-mlogloss:1.49778
[7]	train-mlogloss:1.45955	eval-mlogloss:1.48860
[8]	train-mlogloss:1.44806	eval-mlogloss:1.48003
[9]	train-mlogloss:1.43755	eval-mlogloss:1.47283
[10]	train-mlogloss:1.42808	eval-mlogloss:1.46626
[11]	train-mlogloss:1.41963	eval-mlogloss:1.46050
[12]	train-mlogloss:1.41152	eval-mlogloss:1.45555
[13]	train-mlogloss:1.40410	eval-mlogloss:1.45121
[14]	train-mlogloss:1.39747	eval-mlogloss:1.44742
[15]	train-mlogloss:1.39063	eval-mlogloss:1.44370
[16]	train-mlogloss:1.38481	eval-mlogloss:1.44027
[17]	train-mlogloss:1.37883	eval-mlogloss:1.43713
[18]	train-mlogloss:1.37356	eval-mlogloss:1.43425
[19]	train-mlogloss:1.36869	eval-mlogloss:1.43209
[20]	train

In [8]:
y_pred = xgb1.predict(test)
score_base_xgb = DST_model_report(xgb1)

TypeError: 'module' object is not callable

# Essai Grid base

In [2]:
train = xgb.DMatrix(data= X_train,label = y_train)
test = xgb.DMatrix(data= X_test, label = y_test)

params = {'learning_rate': [0.1, 0.01, 0.05],
          'max_depth': [3, 4, 5, 6],
          'min_child_weight': [1, 3, 5],
          'gamma': [0, 0.1, 0.2],
          'subsample': [0.7, 0.8, 0.9],
          'colsample_bytree': [0.7, 0.8, 0.9],
          'reg_lambda': [0, 1, 10],
          'reg_alpha': [0, 0.1, 1]
}
xgb_clf = XGBClassifier()
grid = GridSearchCV(estimator= xgb_clf, param_grid = params,
                     scoring = 'accuracy', cv = 3,verbose = 3)
grid.fit(X_train, y_train)
# Saving the model
from joblib import dump, load
dump(grid, '../data/XGBoost_grid_base.joblib')
# pour charger le modèle:
# grid_search = load('../data/XGBoost_grid_base.joblib')

# scores:
score_grid_base_xgb = DST_model_report(grid)

# Test avec TFIDF

In [3]:
# Vectorization des avis lémmatisés
X_train = DST_review_vector(train)
X_test = DST_review_vector(test)

train =xgb.DMatrix(data= X_train,label = y_train)
test = xgb.DMatrix(data= X_test, label = y_test)

params = {'learning_rate': [0.1, 0.01, 0.05],
          'max_depth': [3, 4, 5, 6],
          'min_child_weight': [1, 3, 5],
          'gamma': [0, 0.1, 0.2],
          'subsample': [0.7, 0.8, 0.9],
          'colsample_bytree': [0.7, 0.8, 0.9],
          'reg_lambda': [0, 1, 10],
          'reg_alpha': [0, 0.1, 1]}

xgb_clf = XGBClassifier()

grid = GridSearchCV(estimator= xgb_clf, param_grid = params, scoring = 'accuracy', cv = 3,
                    verbose = 3)
grid.fit(X_train, y_train)

Fitting 3 folds for each of 8748 candidates, totalling 26244 fits
[CV 1/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=3, min_child_weight=1, reg_alpha=0, reg_lambda=0, subsample=0.7;, score=0.671 total time=   2.9s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=3, min_child_weight=1, reg_alpha=0, reg_lambda=0, subsample=0.7;, score=0.660 total time=   2.9s
[CV 3/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=3, min_child_weight=1, reg_alpha=0, reg_lambda=0, subsample=0.7;, score=0.652 total time=   2.7s
[CV 1/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=3, min_child_weight=1, reg_alpha=0, reg_lambda=0, subsample=0.8;, score=0.670 total time=   2.7s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=3, min_child_weight=1, reg_alpha=0, reg_lambda=0, subsample=0.8;, score=0.659 total time=   2.7s
[CV 3/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.1, max_depth=3, min_chil

GridSearchCV(cv=3,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None, device=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     feature_types=None, gamma=None,
                                     grow_policy=None, importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None,...
                                     missing=nan, monotone_constraints=None,
                                     multi_strategy=None, n_estimators=None,
                                     n_jobs=None, num_parallel_tree=None,
                                     random_state=None, ...),
             param_grid={'colsample_bytree': [0.7, 0.8, 0.9],
                         'gamma': [0, 0.1, 0.2],
                         'learning_rate': [0.1, 0.01, 0.05],
                         'max_depth': [3, 4, 5, 6],
                         'min_child_weight': [1, 3, 5],
                         'reg_alpha': [0, 0.1, 1], 'reg_lambda': [0, 1, 10],
                         'subsample': [0.7, 0.8, 0.9]},
             scoring='accuracy', verbose=3)

In [4]:
# Saving the model
from joblib import dump, load

# After your grid search has completed
dump(grid, '../data/XGBoost_grid_tfidf.joblib')
score_grid_tfidf_xgb = DST_model_report(grid)
# pour charger le modèle:
# grid_search = load('../data/XGBoost_grid_tfidf.joblib')

['../data/XGBoost_grid_tfidf.joblib']